In [1]:
#test the litter set
import numpy as np
from sklearn.metrics import accuracy_score #works
from sklearn.cluster import KMeans
from tensorflow.keras.datasets import mnist

from time import time
import numpy as np
import tensorflow.keras.backend as K
from tensorflow.keras.layers import Dense, Input,Layer, InputSpec
from tensorflow.keras.models import Model
from tensorflow.keras.optimizers import SGD
from tensorflow.keras import callbacks
from tensorflow.keras.initializers import VarianceScaling
from sklearn.cluster import KMeans
import metrics

print(__import__('sys').version)

3.6.8 |Anaconda, Inc.| (default, Dec 30 2018, 01:22:34) 
[GCC 7.3.0]


In [2]:
(x_train, y_train), (x_test, y_test) = mnist.load_data()
x = np.concatenate((x_train, x_test))
y = np.concatenate((y_train, y_test))
x = x.reshape((x.shape[0], -1))
x = np.divide(x, 255.)
# 10 clusters
n_clusters = len(np.unique(y))
# Runs in parallel 4 CPUs
kmeans = KMeans(n_clusters=n_clusters, n_init=20, n_jobs=4)
# Train K-Means.
#y_pred_kmeans = kmeans.fit_predict(x)
# Evaluate the K-Means clustering accuracy.


In [ ]:
print(accuracy_score(y, y_pred_kmeans))
metrics.acc(y, y_pred_kmeans)

In [3]:
def autoencoder(dims, act='relu', init='glorot_uniform'):
    """
    Fully connected auto-encoder model, symmetric.
    Arguments:
        dims: list of number of units in each layer of encoder. dims[0] is input dim, dims[-1] is units in hidden layer.
            The decoder is symmetric with encoder. So number of layers of the auto-encoder is 2*len(dims)-1
        act: activation, not applied to Input, Hidden and Output layers
    return:
        (ae_model, encoder_model), Model of autoencoder and model of encoder
    """
    n_stacks = len(dims) - 1
    # input
    input_img = Input(shape=(dims[0],), name='input')
    x = input_img
    # internal layers in encoder
    for i in range(n_stacks-1):
        x = Dense(dims[i + 1], activation=act, kernel_initializer=init, name='encoder_%d' % i)(x)

    # hidden layer
    encoded = Dense(dims[-1], kernel_initializer=init, name='encoder_%d' % (n_stacks - 1))(x)  # hidden layer, features are extracted from here

    x = encoded
    # internal layers in decoder
    for i in range(n_stacks-1, 0, -1):
        x = Dense(dims[i], activation=act, kernel_initializer=init, name='decoder_%d' % i)(x)

    # output
    x = Dense(dims[0], kernel_initializer=init, name='decoder_0')(x)
    decoded = x
    return Model(inputs=input_img, outputs=decoded, name='AE'), Model(inputs=input_img, outputs=encoded, name='encoder')


In [4]:
(x_train, y_train), (x_test, y_test) = mnist.load_data()
print(x_train.shape)
print(x_test.shape)
x = np.concatenate((x_train, x_test))
y = np.concatenate((y_train, y_test))
x = x.reshape((x.shape[0], -1))
x = np.divide(x, 255.)
x.shape

(60000, 28, 28)
(10000, 28, 28)


(70000, 784)

In [5]:
n_clusters = len(np.unique(y))
print(n_clusters)
x.shape

10


(70000, 784)

In [6]:
dims = [x.shape[-1], 500, 500, 2000, 10]
init = VarianceScaling(scale=1. / 3., mode='fan_in',
                           distribution='uniform')
pretrain_optimizer = SGD(lr=1, momentum=0.9)
pretrain_epochs = 300
batch_size = 256
save_dir = './results'

In [7]:
autoencoder, encoder = autoencoder(dims, init=init)

In [8]:
#from tensorflow.keras.utils import plot_model
#plot_model(autoencoder, to_file='autoencoder.png', show_shapes=True)
#from IPython.display import Image
#Image(filename='autoencoder.png') 

In [17]:
autoencoder.compile(optimizer=pretrain_optimizer, loss='mse')
autoencoder.fit(x, x, batch_size=batch_size, epochs=pretrain_epochs) #, callbacks=cb)
autoencoder.save_weights(save_dir + '/ae_weights.h5')

Instructions for updating:
Use tf.cast instead.
Instructions for updating:
Use tf.cast instead.
Epoch 1/300
70000/70000 [==============================] - 20s 286us/sample - loss: 0.0646
Epoch 2/300
70000/70000 [==============================] - 1s 16us/sample - loss: 0.0436
Epoch 3/300
70000/70000 [==============================] - 1s 17us/sample - loss: 0.0318
Epoch 4/300
70000/70000 [==============================] - 1s 15us/sample - loss: 0.0266
Epoch 5/300
70000/70000 [==============================] - 1s 17us/sample - loss: 0.0239
Epoch 6/300
70000/70000 [==============================] - 1s 17us/sample - loss: 0.0223
Epoch 7/300
70000/70000 [==============================] - 1s 16us/sample - loss: 0.0211
Epoch 8/300
70000/70000 [==============================] - 1s 16us/sample - loss: 0.0202
Epoch 9/300
70000/70000 [==============================] - 1s 18us/sample - loss: 0.0195
Epoch 10/300
70000/70000 [==============================] - 2s 22us/sample - loss: 0.0189
Epoch 11/30

70000/70000 [==============================] - 1s 15us/sample - loss: 0.0109
Epoch 87/300
70000/70000 [==============================] - 1s 15us/sample - loss: 0.0109
Epoch 88/300
70000/70000 [==============================] - 1s 15us/sample - loss: 0.0109
Epoch 89/300
70000/70000 [==============================] - 1s 15us/sample - loss: 0.0108
Epoch 90/300
70000/70000 [==============================] - 1s 15us/sample - loss: 0.0108
Epoch 91/300
70000/70000 [==============================] - 1s 15us/sample - loss: 0.0108
Epoch 92/300
70000/70000 [==============================] - 1s 16us/sample - loss: 0.0108
Epoch 93/300
70000/70000 [==============================] - 1s 16us/sample - loss: 0.0107
Epoch 94/300
70000/70000 [==============================] - 1s 15us/sample - loss: 0.0107
Epoch 95/300
70000/70000 [==============================] - 1s 15us/sample - loss: 0.0107
Epoch 96/300
70000/70000 [==============================] - 1s 15us/sample - loss: 0.0106
Epoch 97/300
70000/7000

70000/70000 [==============================] - 1s 15us/sample - loss: 0.0084
Epoch 267/300
70000/70000 [==============================] - 1s 15us/sample - loss: 0.0084
Epoch 268/300
70000/70000 [==============================] - 1s 15us/sample - loss: 0.0084
Epoch 269/300
70000/70000 [==============================] - 1s 15us/sample - loss: 0.0084
Epoch 270/300
70000/70000 [==============================] - 1s 15us/sample - loss: 0.0084
Epoch 271/300
70000/70000 [==============================] - 1s 15us/sample - loss: 0.0084
Epoch 272/300
70000/70000 [==============================] - 1s 15us/sample - loss: 0.0084
Epoch 273/300
70000/70000 [==============================] - 1s 16us/sample - loss: 0.0084
Epoch 274/300
70000/70000 [==============================] - 1s 17us/sample - loss: 0.0084
Epoch 275/300
70000/70000 [==============================] - 1s 17us/sample - loss: 0.0084
Epoch 276/300
70000/70000 [==============================] - 1s 16us/sample - loss: 0.0084
Epoch 277/300

OSError: Unable to create file (unable to open file: name = './results/ae_weights.h5', errno = 2, error message = 'No such file or directory', flags = 13, o_flags = 242)

In [19]:
autoencoder.save_weights(save_dir + '/ae_weights.h5')

In [11]:
from tensorflow.keras.models import Model
from tensorflow.keras import backend as K
from tensorflow.keras import layers
from tensorflow.keras.layers import Input, Dense, Conv2D, MaxPooling2D, UpSampling2D, Flatten, Reshape, Conv2DTranspose
from tensorflow.keras.models import Model
import numpy as np

In [12]:
def autoencoderConv2D_1(input_shape=(64, 64, 3), filters=[32, 64, 128, 1000]):
    input_img = Input(shape=input_shape)
    if input_shape[0] % 8 == 0:
        pad3 = 'same'
    else:
        pad3 = 'valid'
    x = Conv2D(filters[0], 5, strides=2, padding='same', activation='relu', name='conv1', input_shape=input_shape)(input_img)

    x = Conv2D(filters[1], 5, strides=2, padding='same', activation='relu', name='conv2')(x)

    x = Conv2D(filters[2], 3, strides=2, padding=pad3, activation='relu', name='conv3')(x)

    x = Flatten()(x)
    encoded = Dense(units=filters[3], name='embedding')(x)
    x = Dense(units=filters[2]*int(input_shape[0]/8)*int(input_shape[0]/8), activation='relu')(encoded)

    x = Reshape((int(input_shape[0]/8), int(input_shape[0]/8), filters[2]))(x)
    x = Conv2DTranspose(filters[1], 3, strides=2, padding=pad3, activation='relu', name='deconv3')(x)

    x = Conv2DTranspose(filters[0], 5, strides=2, padding='same', activation='relu', name='deconv2')(x)

    decoded = Conv2DTranspose(input_shape[2], 5, strides=2, padding='same', name='deconv1')(x)
    return Model(inputs=input_img, outputs=decoded, name='AE'), Model(inputs=input_img, outputs=encoded, name='encoder')
autoencoder, encoder = autoencoderConv2D_1()
autoencoder.summary()

Model: "AE"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_2 (InputLayer)         [(None, 64, 64, 3)]       0         
_________________________________________________________________
conv1 (Conv2D)               (None, 32, 32, 32)        2432      
_________________________________________________________________
conv2 (Conv2D)               (None, 16, 16, 64)        51264     
_________________________________________________________________
conv3 (Conv2D)               (None, 8, 8, 128)         73856     
_________________________________________________________________
flatten (Flatten)            (None, 8192)              0         
_________________________________________________________________
embedding (Dense)            (None, 1000)              8193000   
_________________________________________________________________
dense (Dense)                (None, 8192)              8200192  

In [13]:
autoencoder.load_weights(save_dir + '/firstAutoEncoder.h5')

In [41]:
class ClusteringLayer(Layer):
    """
    Clustering layer converts input sample (feature) to soft label, i.e. a vector that represents the probability of the
    sample belonging to each cluster. The probability is calculated with student's t-distribution.

    # Example
    ```
        model.add(ClusteringLayer(n_clusters=10))
    ```
    # Arguments
        n_clusters: number of clusters.
        weights: list of Numpy array with shape `(n_clusters, n_features)` witch represents the initial cluster centers.
        alpha: degrees of freedom parameter in Student's t-distribution. Default to 1.0.
    # Input shape
        2D tensor with shape: `(n_samples, n_features)`.
    # Output shape
        2D tensor with shape: `(n_samples, n_clusters)`.
    """

    def __init__(self, n_clusters, weights=None, alpha=1.0, **kwargs):
        if 'input_shape' not in kwargs and 'input_dim' in kwargs:
            kwargs['input_shape'] = (kwargs.pop('input_dim'),)
        super(ClusteringLayer, self).__init__(**kwargs)
        self.n_clusters = n_clusters
        self.alpha = alpha
        self.initial_weights = weights
        self.input_spec = InputSpec(ndim=2)

    def build(self, input_shape):
        assert len(input_shape) == 2
        input_dim = input_shape[1]
        self.input_spec = InputSpec(dtype=K.floatx(), shape=(None, input_dim))
        self.clusters = self.add_weight(name="clustering", shape = (int(self.n_clusters), int(input_dim)), initializer='glorot_uniform',trainable=True)
        if self.initial_weights is not None:
            self.set_weights(self.initial_weights)
            del self.initial_weights
        self.built = True

    def call(self, inputs, **kwargs):
        """ student t-distribution, as same as used in t-SNE algorithm.
         Measure the similarity between embedded point z_i and centroid µ_j.
                 q_ij = 1/(1+dist(x_i, µ_j)^2), then normalize it.
                 q_ij can be interpreted as the probability of assigning sample i to cluster j.
                 (i.e., a soft assignment)
        Arguments:
            inputs: the variable containing data, shape=(n_samples, n_features)
        Return:
            q: student's t-distribution, or soft labels for each sample. shape=(n_samples, n_clusters)
        """
        q = 1.0 / (1.0 + (K.sum(K.square(K.expand_dims(inputs, axis=1) - self.clusters), axis=2) / self.alpha))
        q **= (self.alpha + 1.0) / 2.0
        q = K.transpose(K.transpose(q) / K.sum(q, axis=1)) # Make sure each sample's 10 values add up to 1.
        return q

    def compute_output_shape(self, input_shape):
        assert input_shape and len(input_shape) == 2
        return input_shape[0], self.n_clusters

    def get_config(self):
        config = {'n_clusters': self.n_clusters}
        base_config = super(ClusteringLayer, self).get_config()
        return dict(list(base_config.items()) + list(config.items()))

In [47]:
clustering_layer = ClusteringLayer(n_clusters, name='clustering')(encoder.output)
model = Model(inputs=encoder.input, outputs=clustering_layer)

In [48]:
model.compile(optimizer=SGD(0.01, 0.9), loss='kld')

In [49]:
kmeans = KMeans(n_clusters=n_clusters, n_init=20)
y_pred = kmeans.fit_predict(encoder.predict(x))

In [50]:
y_pred_last = np.copy(y_pred)

In [51]:
model.get_layer(name='clustering').set_weights([kmeans.cluster_centers_])

In [52]:
# computing an auxiliary target distribution
def target_distribution(q):
    weight = q ** 2 / q.sum(0)
    return (weight.T / weight.sum(1)).T

In [53]:
loss = 0
index = 0
maxiter = 8000
update_interval = 140
index_array = np.arange(x.shape[0])

In [54]:
tol = 0.001 # tolerance threshold to stop training

In [55]:
for ite in range(int(maxiter)):
    if ite % update_interval == 0:
        q = model.predict(x, verbose=0)
        p = target_distribution(q)  # update the auxiliary target distribution p

        # evaluate the clustering performance
        y_pred = q.argmax(1)
        if y is not None:
            acc = np.round(metrics.acc(y, y_pred), 5)
            nmi = np.round(metrics.nmi(y, y_pred), 5)
            ari = np.round(metrics.ari(y, y_pred), 5)
            loss = np.round(loss, 5)
            print('Iter %d: acc = %.5f, nmi = %.5f, ari = %.5f' % (ite, acc, nmi, ari), ' ; loss=', loss)

        # check stop criterion - model convergence
        delta_label = np.sum(y_pred != y_pred_last).astype(np.float32) / y_pred.shape[0]
        y_pred_last = np.copy(y_pred)
        if ite > 0 and delta_label < tol:
            print('delta_label ', delta_label, '< tol ', tol)
            print('Reached tolerance threshold. Stopping training.')
            break
    idx = index_array[index * batch_size: min((index+1) * batch_size, x.shape[0])]
    loss = model.train_on_batch(x=x[idx], y=p[idx])
    index = index + 1 if (index + 1) * batch_size <= x.shape[0] else 0

model.save_weights(save_dir + '/DEC_model_final.h5')

/home/king/anaconda3/lib/python3.7/site-packages/sklearn/metrics/cluster/supervised.py:844: FutureWarning: The behavior of NMI will change in version 0.22. To match the behavior of 'v_measure_score', NMI will use average_method='arithmetic' by default.
  FutureWarning)


Iter 0: acc = 0.91256, nmi = 0.82029, ari = 0.81521  ; loss= 0
Iter 140: acc = 0.92089, nmi = 0.83093, ari = 0.83332  ; loss= 0.04619
Iter 280: acc = 0.93281, nmi = 0.85022, ari = 0.85777  ; loss= 0.15459
Iter 420: acc = 0.94059, nmi = 0.86294, ari = 0.87380  ; loss= 0.2047
Iter 560: acc = 0.94543, nmi = 0.87193, ari = 0.88383  ; loss= 0.21731
Iter 700: acc = 0.94887, nmi = 0.87776, ari = 0.89094  ; loss= 0.21237
Iter 840: acc = 0.95151, nmi = 0.88263, ari = 0.89639  ; loss= 0.20751
Iter 980: acc = 0.95300, nmi = 0.88542, ari = 0.89950  ; loss= 0.20571
Iter 1120: acc = 0.95427, nmi = 0.88787, ari = 0.90218  ; loss= 0.19575
Iter 1260: acc = 0.95507, nmi = 0.88937, ari = 0.90386  ; loss= 0.19596
Iter 1400: acc = 0.95580, nmi = 0.89090, ari = 0.90536  ; loss= 0.19036
Iter 1540: acc = 0.95640, nmi = 0.89227, ari = 0.90663  ; loss= 0.17978
Iter 1680: acc = 0.95674, nmi = 0.89285, ari = 0.90733  ; loss= 0.17421
Iter 1820: acc = 0.95733, nmi = 0.89427, ari = 0.90855  ; loss= 0.18425
Iter 1960

In [56]:
model.load_weights(save_dir + '/DEC_model_final.h5')

In [57]:
# Eval.
q = model.predict(x, verbose=0)
p = target_distribution(q)  # update the auxiliary target distribution p

# evaluate the clustering performance
y_pred = q.argmax(1)
if y is not None:
    acc = np.round(metrics.acc(y, y_pred), 5)
    nmi = np.round(metrics.nmi(y, y_pred), 5)
    ari = np.round(metrics.ari(y, y_pred), 5)
    loss = np.round(loss, 5)
    print('Acc = %.5f, nmi = %.5f, ari = %.5f' % (acc, nmi, ari), ' ; loss=', loss)

Acc = 0.95873, nmi = 0.89781, ari = 0.91153  ; loss= 0.10534


In [58]:
import seaborn as sns
import sklearn.metrics
import matplotlib.pyplot as plt
sns.set(font_scale=3)
confusion_matrix = sklearn.metrics.confusion_matrix(y, y_pred)

plt.figure(figsize=(16, 14))
sns.heatmap(confusion_matrix, annot=True, fmt="d", annot_kws={"size": 20});
plt.title("Confusion matrix", fontsize=30)
plt.ylabel('True label', fontsize=25)
plt.xlabel('Clustering label', fontsize=25)
plt.show()

<Figure size 1600x1400 with 2 Axes>

In [59]:
from sklearn.utils.linear_assignment_ import linear_assignment

y_true = y.astype(np.int64)
D = max(y_pred.max(), y_true.max()) + 1
w = np.zeros((D, D), dtype=np.int64)
# Confusion matrix.
for i in range(y_pred.size):
    w[y_pred[i], y_true[i]] += 1
ind = linear_assignment(-w)

sum([w[i, j] for i, j in ind]) * 1.0 / y_pred.size

0.9587285714285714

In [60]:
w

array([[6795,    2,   32,    3,    4,   28,   31,    8,   18,   28],
       [   1,   29,   52,   53,    8,    3,    0, 6978,    9,  127],
       [  47,   45,  107,   56,    9,   18,   11,    8, 6434,   55],
       [   6,   91, 6674,  113,   16,   19,    5,   97,   41,    4],
       [   5,   13,   51,    1, 6633,    8,   13,   45,   18,   91],
       [   0, 7645,    7,    1,    4,    3,   10,   28,   30,   10],
       [   4,   35,   43, 6820,    0,   91,    0,    8,   98,  124],
       [   6,    2,    2,   76,    0, 6073,  242,    3,   74,   20],
       [  28,    4,   15,    2,   34,   47, 6564,    0,   12,    4],
       [  11,   11,    7,   16,  116,   23,    0,  118,   91, 6495]])

In [61]:
ind

array([[0, 0],
       [1, 7],
       [2, 8],
       [3, 2],
       [4, 4],
       [5, 1],
       [6, 3],
       [7, 5],
       [8, 6],
       [9, 9]])

In [62]:
w.argmax(1)

array([0, 7, 8, 2, 4, 1, 3, 5, 6, 9])

In [19]:
import os
import re
from tensorflow.python.platform import gfile
images_dir = '/home/deep/fashion1/'
key_images = [images_dir+f for f in os.listdir(images_dir) if re.search('jpg|JPG|jpeg|JPEG', f)]
nb_features = 1000
features = np.empty((len(key_images),nb_features))
print(features.shape)

(96946, 1000)


In [20]:
for ind, image in enumerate(key_images):
    if (ind%1 == 0):
        print('Processing %s...' % (image))
    if not gfile.Exists(image):
        tf.logging.fatal('File does not exist %s', image)

    image_data = gfile.FastGFile(image, 'rb').read()
    try:
        predictions = autoencoder.predict(image_data)
        features[ind,:] = np.squeeze(predictions)
    except:
        continue

W0717 16:18:47.556104 140409016514304 deprecation.py:323] From <ipython-input-20-16ce0fdcd91b>:7: FastGFile.__init__ (from tensorflow.python.platform.gfile) is deprecated and will be removed in a future version.
Instructions for updating:
Use tf.gfile.GFile.


Processing /home/deep/fashion1/33680841867.jpeg...
Processing /home/deep/fashion1/33527873665.jpeg...
Processing /home/deep/fashion1/34288306758.jpeg...
Processing /home/deep/fashion1/23170662349.jpeg...
Processing /home/deep/fashion1/34708998661.jpeg...
Processing /home/deep/fashion1/31580795023.jpeg...
Processing /home/deep/fashion1/34572358264.jpeg...
Processing /home/deep/fashion1/100000969588.jpeg...
Processing /home/deep/fashion1/28551110577.jpeg...
Processing /home/deep/fashion1/19110562701.jpeg...
Processing /home/deep/fashion1/30782436215.jpeg...
Processing /home/deep/fashion1/10129816233.jpeg...
Processing /home/deep/fashion1/29973039178.jpeg...
Processing /home/deep/fashion1/34765696303.jpeg...
Processing /home/deep/fashion1/31534849315.jpeg...
Processing /home/deep/fashion1/33019995223.jpg...
Processing /home/deep/fashion1/34550255677.jpeg...
Processing /home/deep/fashion1/32247776543.jpeg...
Processing /home/deep/fashion1/28279881937.jpeg...
Processing /home/deep/fashion1/

Processing /home/deep/fashion1/6538832.jpeg...
Processing /home/deep/fashion1/34109675094.jpeg...
Processing /home/deep/fashion1/32377638178.jpeg...
Processing /home/deep/fashion1/100000682819.jpeg...
Processing /home/deep/fashion1/33407688583.jpeg...
Processing /home/deep/fashion1/34320973910.jpeg...
Processing /home/deep/fashion1/31766944397.jpeg...
Processing /home/deep/fashion1/34870461354.jpeg...
Processing /home/deep/fashion1/32528077412.jpeg...
Processing /home/deep/fashion1/100001060539.jpeg...
Processing /home/deep/fashion1/34684207167.jpeg...
Processing /home/deep/fashion1/35679847075.jpeg...
Processing /home/deep/fashion1/100000127958.jpeg...
Processing /home/deep/fashion1/100000769567.jpeg...
Processing /home/deep/fashion1/34318282596.jpeg...
Processing /home/deep/fashion1/8583432.jpeg...
Processing /home/deep/fashion1/33750165777.jpeg...
Processing /home/deep/fashion1/32653160357.jpeg...
Processing /home/deep/fashion1/34302647727.jpeg...
Processing /home/deep/fashion1/2999

Processing /home/deep/fashion1/100000619021.jpeg...
Processing /home/deep/fashion1/32061958117.jpeg...
Processing /home/deep/fashion1/34721593984.jpeg...
Processing /home/deep/fashion1/25891419256.jpeg...
Processing /home/deep/fashion1/34430495512.jpeg...
Processing /home/deep/fashion1/22925394381.jpeg...
Processing /home/deep/fashion1/31536428320.jpeg...
Processing /home/deep/fashion1/34163884527.jpeg...
Processing /home/deep/fashion1/35553174891.jpeg...
Processing /home/deep/fashion1/33277025745.jpeg...
Processing /home/deep/fashion1/31208526266.jpeg...
Processing /home/deep/fashion1/35785700627.jpeg...
Processing /home/deep/fashion1/100000489756.jpeg...
Processing /home/deep/fashion1/26730747728.jpeg...
Processing /home/deep/fashion1/100000194852.jpeg...
Processing /home/deep/fashion1/33945221969.jpeg...
Processing /home/deep/fashion1/33990017449.jpeg...
Processing /home/deep/fashion1/36019534566.jpeg...
Processing /home/deep/fashion1/33563092140.jpeg...
Processing /home/deep/fashio

Processing /home/deep/fashion1/26342537675.jpeg...
Processing /home/deep/fashion1/16895857525.jpeg...
Processing /home/deep/fashion1/100000877221.jpeg...
Processing /home/deep/fashion1/34209563681.jpeg...
Processing /home/deep/fashion1/8984095.jpeg...
Processing /home/deep/fashion1/34534902624.jpeg...
Processing /home/deep/fashion1/34505419844.jpeg...
Processing /home/deep/fashion1/29372506161.jpeg...
Processing /home/deep/fashion1/32239428158.jpeg...
Processing /home/deep/fashion1/32405821441.jpg...
Processing /home/deep/fashion1/31074431473.jpeg...
Processing /home/deep/fashion1/34592501411.jpeg...
Processing /home/deep/fashion1/31674878665.jpeg...
Processing /home/deep/fashion1/100000656187.jpeg...
Processing /home/deep/fashion1/10723922122.jpeg...
Processing /home/deep/fashion1/33947679829.jpeg...
Processing /home/deep/fashion1/34362107627.jpeg...
Processing /home/deep/fashion1/33223031845.jpeg...
Processing /home/deep/fashion1/32260591416.jpeg...
Processing /home/deep/fashion1/340

...

Processing /home/deep/fashion1/32771204821.jpeg...
Processing /home/deep/fashion1/30403088165.jpeg...
Processing /home/deep/fashion1/32324812599.jpeg...
Processing /home/deep/fashion1/26520582352.jpeg...
Processing /home/deep/fashion1/31985849710.jpeg...
Processing /home/deep/fashion1/34129010815.jpeg...
Processing /home/deep/fashion1/33409806449.jpeg...
Processing /home/deep/fashion1/100001152667.jpeg...
Processing /home/deep/fashion1/17621032454.jpeg...
Processing /home/deep/fashion1/8734183.jpeg...
Processing /home/deep/fashion1/34113034901.jpeg...
Processing /home/deep/fashion1/32045717154.jpeg...
Processing /home/deep/fashion1/34576871606.jpeg...
Processing /home/deep/fashion1/34504687210.jpeg...
Processing /home/deep/fashion1/34979694425.jpeg...
Processing /home/deep/fashion1/33383056957.jpeg...
Processing /home/deep/fashion1/34138498700.jpeg...
Processing /home/deep/fashion1/33673377716.jpeg...
Processing /home/deep/fashion1/31380315118.jpeg...
Processing /home/deep/fashion1/341

Processing /home/deep/fashion1/25858089906.jpeg...
Processing /home/deep/fashion1/35280798902.jpeg...
Processing /home/deep/fashion1/33397538875.jpeg...
Processing /home/deep/fashion1/100001665040.jpeg...
Processing /home/deep/fashion1/26056776181.jpeg...
Processing /home/deep/fashion1/100000770963.jpeg...
Processing /home/deep/fashion1/34476772645.jpeg...
Processing /home/deep/fashion1/34033447704.jpeg...
Processing /home/deep/fashion1/33405293532.jpeg...
Processing /home/deep/fashion1/34687866069.jpeg...
Processing /home/deep/fashion1/33856387413.jpeg...
Processing /home/deep/fashion1/100000080456.jpeg...
Processing /home/deep/fashion1/34950804620.jpeg...
Processing /home/deep/fashion1/31949361507.jpeg...
Processing /home/deep/fashion1/34098899506.jpeg...
Processing /home/deep/fashion1/100000962901.jpeg...
Processing /home/deep/fashion1/100001171815.jpeg...
Processing /home/deep/fashion1/34545373016.jpeg...
Processing /home/deep/fashion1/31581937347.jpeg...
Processing /home/deep/fash

Processing /home/deep/fashion1/34836124861.jpeg...
Processing /home/deep/fashion1/33279200759.jpeg...
Processing /home/deep/fashion1/8259667.jpeg...
Processing /home/deep/fashion1/33779936252.jpeg...
Processing /home/deep/fashion1/32453077665.jpeg...
Processing /home/deep/fashion1/33406399336.jpeg...
Processing /home/deep/fashion1/31060366663.jpg...
Processing /home/deep/fashion1/28222236116.jpeg...
Processing /home/deep/fashion1/33965527835.jpeg...
Processing /home/deep/fashion1/17970273480.jpeg...
Processing /home/deep/fashion1/34133868501.jpeg...
Processing /home/deep/fashion1/34851849108.jpeg...
Processing /home/deep/fashion1/35028848167.jpeg...
Processing /home/deep/fashion1/22863058379.jpeg...
Processing /home/deep/fashion1/33219405473.jpeg...
Processing /home/deep/fashion1/34764885592.jpeg...
Processing /home/deep/fashion1/34672513514.jpeg...
Processing /home/deep/fashion1/31026485463.jpeg...
Processing /home/deep/fashion1/34589353406.jpeg...
Processing /home/deep/fashion1/31343

Processing /home/deep/fashion1/8762450.jpeg...
Processing /home/deep/fashion1/100000354320.jpeg...
Processing /home/deep/fashion1/34235934822.jpeg...
Processing /home/deep/fashion1/30160674135.jpeg...
Processing /home/deep/fashion1/17363653987.jpeg...
Processing /home/deep/fashion1/100000977340.jpeg...
Processing /home/deep/fashion1/30229541106.jpeg...
Processing /home/deep/fashion1/100000126136.jpeg...
Processing /home/deep/fashion1/25659117427.jpeg...
Processing /home/deep/fashion1/33779680088.jpeg...
Processing /home/deep/fashion1/30314314075.jpeg...
Processing /home/deep/fashion1/34539660554.jpeg...
Processing /home/deep/fashion1/16180281383.jpeg...
Processing /home/deep/fashion1/33614033124.jpeg...
Processing /home/deep/fashion1/31382434539.jpeg...
Processing /home/deep/fashion1/100001228817.jpeg...
Processing /home/deep/fashion1/33698345612.jpg...
Processing /home/deep/fashion1/33278797202.jpeg...
Processing /home/deep/fashion1/34493430578.jpeg...
Processing /home/deep/fashion1/3

Processing /home/deep/fashion1/34557034907.jpeg...
Processing /home/deep/fashion1/34191297795.jpeg...
Processing /home/deep/fashion1/35463241377.jpeg...
Processing /home/deep/fashion1/33552171699.jpeg...
Processing /home/deep/fashion1/33675621305.jpeg...
Processing /home/deep/fashion1/33985029179.jpeg...
Processing /home/deep/fashion1/34493086461.jpeg...
Processing /home/deep/fashion1/8772276.jpeg...
Processing /home/deep/fashion1/30688683544.jpeg...
Processing /home/deep/fashion1/34834780147.jpeg...
Processing /home/deep/fashion1/25647517000.jpeg...
Processing /home/deep/fashion1/33474357876.jpeg...
Processing /home/deep/fashion1/100000746398.jpeg...
Processing /home/deep/fashion1/35295004747.jpeg...
Processing /home/deep/fashion1/32163870826.jpeg...
Processing /home/deep/fashion1/35590600113.jpeg...
Processing /home/deep/fashion1/100001083444.jpeg...
Processing /home/deep/fashion1/33124514729.jpeg...
Processing /home/deep/fashion1/31021018610.jpeg...
Processing /home/deep/fashion1/32

In [21]:
print(features.shape)

(96946, 1000)


In [ ]:
from sklearn import cluster, datasets
k_means = cluster.KMeans(n_clusters=20000,algorithm="full")
k_means.fit(features) 